In [2]:
import json
import numpy as np
import pandas as pd
import requests
import ast


In [2]:
df = pd.DataFrame.from_dict(json.loads(open('../data/interim/urls.json').read()), orient='index', columns=['redirect'])
df = df.reset_index()
df.rename(columns={'index': 'url'}, inplace=True)
df.drop('redirect', axis=1, inplace=True)
df

url
0                              http://sidc.be/silso/home
1                                       https://bmrb.io/
2      http://www.pac.dfo-mpo.gc.ca/science/oceans/da...
3                         https://www.cpc.ncep.noaa.gov/
4      http://cosmos.bot.kyoto-u.ac.jp/acytodb//cgi-b...
...                                                  ...
13352    http://radar.brookes.ac.uk/radar/access/home.do
13353                   http://www.ub.uni-siegen.de/opus
13354  http://numerique.bibliotheque.toulouse.fr/cgi-...
13355                    https://www.utas.edu.au/library
13356                 http://204.232.200.153:8080/jspui/

[13357 rows x 1 columns]

In [3]:
df.describe()

url
count                       13357
unique                      13357
top     http://sidc.be/silso/home
freq                            1

In [8]:
def resolve(url):
    print(url)
    timeout = 30
    head_final_code = head_url = head_chain = head_codes = head_elapsed = head_error = get_final_code = get_url = get_chain = get_codes = get_elapsed = get_error = ''

    try:
        head = requests.head(url, timeout=timeout, allow_redirects=True)
        head_final_code = head.status_code
        head_url = head.url
        head_chain = [res.url for res in head.history]
        head_codes = [res.status_code for res in head.history]
        head_elapsed = head.elapsed.total_seconds()
    except Exception as e:
        head_error = e
    
    try:
        get = requests.get(url, timeout=timeout, allow_redirects=True)
        get_final_code = get.status_code
        get_url = get.url
        get_chain = [res.url for res in get.history]
        get_codes = [res.status_code for res in get.history]
        get_elapsed = get.elapsed.total_seconds()
    except Exception as e:
        get_error = e

    return dict(url=url,
                head_final_code=head_final_code, 
                head_url=head_url, 
                head_chain=head_chain, 
                head_codes=head_codes, 
                head_elapsed=head_elapsed, 
                head_error=head_error, 
                get_final_code=get_final_code, 
                get_url=get_url, 
                get_chain=get_chain, 
                get_codes=get_codes,
                get_elapsed=get_elapsed, 
                get_error=get_error)

In [9]:
resolve('https://doi.org/10.1007/978-3-030-30760-8_15')

https://doi.org/10.1007/978-3-030-30760-8_15


{'url': 'https://doi.org/10.1007/978-3-030-30760-8_15',
 'head_final_code': 200,
 'head_url': 'https://link.springer.com/chapter/10.1007/978-3-030-30760-8_15',
 'head_chain': ['https://doi.org/10.1007/978-3-030-30760-8_15',
  'http://link.springer.com/10.1007/978-3-030-30760-8_15',
  'https://link.springer.com/chapter/10.1007/978-3-030-30760-8_15',
  'https://idp.springer.com/authorize?response_type=cookie&client_id=springerlink&redirect_uri=https%3A%2F%2Flink.springer.com%2Fchapter%2F10.1007%2F978-3-030-30760-8_15'],
 'head_codes': [302, 301, 303, 302],
 'head_elapsed': 1.312367,
 'head_error': '',
 'get_final_code': 200,
 'get_url': 'https://link.springer.com/chapter/10.1007/978-3-030-30760-8_15',
 'get_chain': ['https://doi.org/10.1007/978-3-030-30760-8_15',
  'http://link.springer.com/10.1007/978-3-030-30760-8_15',
  'https://link.springer.com/chapter/10.1007/978-3-030-30760-8_15',
  'https://idp.springer.com/authorize?response_type=cookie&client_id=springerlink&redirect_uri=https%

In [8]:
for index, row in df.iterrows():
        if 'get_final_code' not in row or pd.isna(row['get_final_code']):
            res = resolve(row['url'])
            for key in res:
                df.at[index, key] = str(res[key])

http://sidc.be/silso/home
https://bmrb.io/
http://www.pac.dfo-mpo.gc.ca/science/oceans/data-donnees/index-eng.html
https://www.cpc.ncep.noaa.gov/
http://cosmos.bot.kyoto-u.ac.jp/acytodb//cgi-bin/index.cgi?org=as
https://www.geochron.org/
http://ipt.taibif.tw/
https://www.ars-grin.gov/
https://data.seaiceportal.de
http://arabidopsis.info
https://isoarch.eu/
http://epi.minsal.cl/bases-de-datos/
https://tbindia.indiancst.com/GPMSTBTransportal/
https://www.chinare.org.cn/en/
https://brainbase.io
https://obis.org/
https://portal.conp.ca
https://aeronet.gsfc.nasa.gov/new_web/data.html
https://arch.library.northwestern.edu/
https://www.cvrgrid.org/
https://codeocean.com
https://disc.gsfc.nasa.gov
http://metabolonote.kazusa.or.jp
https://www.ncbi.nlm.nih.gov/genbank/
https://www.nist.gov/pml/atomic-spectra-database
https://www.trackhubregistry.org/
http://www.flyrnai.org/
http://www.hgvd.genome.med.kyoto-u.ac.jp/
https://fantom.gsc.riken.jp/
https://ladsweb.modaps.eosdis.nasa.gov/
http://archi

In [47]:
df

url head_final_code  \
0                              http://sidc.be/silso/home             200   
1                                       https://bmrb.io/             200   
2      http://www.pac.dfo-mpo.gc.ca/science/oceans/da...             200   
3                         https://www.cpc.ncep.noaa.gov/             200   
4      http://cosmos.bot.kyoto-u.ac.jp/acytodb//cgi-b...             404   
...                                                  ...             ...   
13352    http://radar.brookes.ac.uk/radar/access/home.do             200   
13353                   http://www.ub.uni-siegen.de/opus             200   
13354  http://numerique.bibliotheque.toulouse.fr/cgi-...                   
13355                    https://www.utas.edu.au/library             200   
13356                 http://204.232.200.153:8080/jspui/                   

                                           head_redirect  \
0                         https://www.sidc.be/silso/home   
1                                       https://bmrb.io/   
2      https://www.pac.dfo-mpo.gc.ca/science/oceans/d...   
3                         https://www.cpc.ncep.noaa.gov/   
4      http://cosmos.bot.kyoto-u.ac.jp/acytodb//cgi-b...   
...                                                  ...   
13352          https://radar.brookes.ac.uk/radar/home.do   
13353                 https://www.ub.uni-siegen.de/opus/   
13354                                                      
13355                    https://www.utas.edu.au/library   
13356                                                      

                                              head_chain       head_codes  \
0                          ['http://sidc.be/silso/home']            [302]   
1                                                     []               []   
2      ['http://www.pac.dfo-mpo.gc.ca/science/oceans/...            [307]   
3                                                     []               []   
4                                                     []               []   
...                                                  ...              ...   
13352  ['http://radar.brookes.ac.uk/radar/access/home...  [302, 302, 302]   
13353  ['http://www.ub.uni-siegen.de/opus', 'https://...       [301, 301]   
13354                                                                       
13355                                                 []               []   
13356                                                                       

      head_elapsed                                         head_error  \
0         0.151548                                                      
1         0.527131                                                      
2         0.530466                                                      
3         0.507708                                                      
4         0.586088                                                      
...            ...                                                ...   
13352     0.082406                                                      
13353     0.056328                                                      
13354               HTTPConnectionPool(host='numerique.bibliothequ...   
13355     0.223856                                                      
13356               HTTPConnectionPool(host='204.232.200.153', por...   

      get_final_code                                       get_redirect  \
0                200                     https://www.sidc.be/silso/home   
1                200                                   https://bmrb.io/   
2                200  https://www.pac.dfo-mpo.gc.ca/science/oceans/d...   
3                200                     https://www.cpc.ncep.noaa.gov/   
4                404  http://cosmos.bot.kyoto-u.ac.jp/acytodb//cgi-b...   
...              ...                                                ...   
13352            200          https://radar.brookes.ac.uk/radar/home.do   
13353            

In [12]:
df.describe()

url head_final_code head_redirect head_chain  \
count                       13357           13357         13357      13357   
unique                      13357              19          9332       4057   
top     http://sidc.be/silso/home             200                       []   
freq                            1            9976          2431       6596   

       head_codes head_elapsed head_error get_final_code get_redirect  \
count       13357        13357      13357          13357        13357   
unique         60        10894       2301             18         9354   
top            []                                    200                
freq         6596         2431      10926          10139         2403   

       get_chain get_codes get_elapsed get_error  
count      13357     13357       13357     13357  
unique      4083        58       10907      2303  
top           []        []                        
freq        6595      6595        2403     10954

In [42]:
df.to_csv('../data/processed/redirects_new.tsv', sep='\t', index=False)

In [20]:
resolve('http://content.wsulibs.wsu.edu')

http://content.wsulibs.wsu.edu


{'url': 'http://content.wsulibs.wsu.edu',
 'head_final_code': 404,
 'head_url': 'https://www.oclc.org/url/?404;http://content.wsulibs.wsu.edu/',
 'head_chain': ['http://content.wsulibs.wsu.edu/'],
 'head_codes': [302],
 'head_elapsed': 1.345008,
 'head_error': '',
 'get_final_code': 404,
 'get_url': 'https://www.oclc.org/url/notfound',
 'get_chain': ['http://content.wsulibs.wsu.edu/',
  'https://www.oclc.org/url/?404;http://content.wsulibs.wsu.edu/'],
 'get_codes': [302, 302],
 'get_elapsed': 0.192602,
 'get_error': ''}